In [2]:
import requests
import time
import re
import pandas as pd
import numpy as np
import random
import pickle
import glob
import os
from bs4 import BeautifulSoup

In [18]:
#with open('kicktraq_data.pickle', 'rb') as f:
#    projects = pickle.load(f)

In [19]:
#projects=pd.read_csv('kicktraq_data.csv', names=['kickstarter_page','funding', 'campaign_dates', 'backers', 'category'])

In [20]:
#projects_from_pickle.campaign_dates.iloc[2]

##### Build projects dataframe from kicktraq page CSVs

In [21]:
#all_page_numbers = range(1,7888)
page_numbers = range(3000,7888)
projects=pd.DataFrame(columns=['kickstarter_page','funding', 'campaign_dates', 'backers', 'category'])
col_types = {'kickstarter_page': 'str','funding': 'str', 'campaign_dates': 'str', 'backers': 'str', 'category': 'str'}

#for file in ['kicktraq_files/kicktraq_page_num21','kicktraq_files/kicktraq_page_num22']:
#for file in glob('kicktraq_files/*'):
for page_num in page_numbers:
    #test if file for this page already exists
    filename = 'kicktraq_files/kicktraq_page_num' + str(page_num)

    page_df = pd.read_csv(filename, dtype=col_types)
    projects = pd.concat([projects, page_df])

##### Check for duplicate rows in projects dataframe

In [22]:
#check for duplicates
print(projects.kickstarter_page.shape)
print(projects.kickstarter_page.unique().shape)
shape1 = projects.kickstarter_page.shape
shape2 = projects.kickstarter_page.unique().shape
if shape1 != shape2:
    projects.drop_duplicates(subset='kickstarter_page', inplace=True)

(72994,)
(72994,)


##### Initialize columns for kickstarter data with base values

In [23]:
projects['description_length'] = 0
projects['n_pledges'] = 0
projects['pledge_level_min'] = 0
projects['pledge_level_max'] = 0
projects['pledge_level_stddev'] = 0
projects['currency'] = '$'

In [24]:
def get_kickstarter_data(proj_series):
    url = 'https://www.kickstarter.com/' + proj_series.kickstarter_page
    #print(url)    
    
    #define filename for where to store html txt file
    page_id_regex = re.compile('projects\/.*\/(.*)\/')
    match = re.search(page_id_regex, proj_series.kickstarter_page)
    page_id = match.group(1)
    filename = r"kickstarter_files/{}.txt".format(page_id)
    
    #check if html txt file exists already
    if  not os.path.isfile(filename):
        print('could not find ' + filename)
        return proj_series

    else:
        with open( filename, "r") as f:
            page_text = f.read()
        soup = BeautifulSoup(page_text,'lxml')
            
    pledges = soup.find_all(class_='pledge__info')

    n_pledges = len(pledges)

    pledge_amounts=[]
    for pledge in pledges:
        pledge_amount = str(pledge.find(class_='money').text.replace('$',''))
        currency = ''
        #while the first character in pledge_amount is not an integer
        while not (re.match('\d',pledge_amount[0])):
            currency = currency + (pledge_amount[0])
            pledge_amount = pledge_amount[1:]
        if currency == '':
            currency = '$'
        proj_series['currency'] = currency
        pledge_amounts.append(int(pledge_amount.replace(',','')))

    try:
        descript_paragraphs = soup.find(class_="full-description js-full-description responsive-media formatted-lists").find_all('p')
        description_words = 0
        for par in descript_paragraphs:
            description_words += len(str(par.text).split())

        proj_series.description_length = description_words
        proj_series.n_pledges = n_pledges
        proj_series.pledge_level_min = min(pledge_amounts)
        proj_series.pledge_level_max = max(pledge_amounts)
        proj_series.pledge_level_stddev = np.std(pledge_amounts)
    except:
        print('something went wrong with' + filename)
        pass
        
    return proj_series


In [25]:
projects = projects.apply(get_kickstarter_data, axis=1)

something went wrong withkickstarter_files/my-audio-sketchbook-belens-debut-album.txt
something went wrong withkickstarter_files/shareroller-first-portable-motor-for-share-bikes-a.txt
something went wrong withkickstarter_files/fire-spirits.txt
something went wrong withkickstarter_files/music-tuned-to-resonate-with-your-body-and-nature.txt
something went wrong withkickstarter_files/escape-from-cubicleland.txt
something went wrong withkickstarter_files/on-location-in-memoriam-project-friday-the-13th-pa.txt
something went wrong withkickstarter_files/the-twisted-tales-boutique.txt
could not find kickstarter_files/educational-and-fun-board-game.txt
could not find kickstarter_files/earth-alliance-a-sci-fi-comic-book-relaunch.txt
could not find kickstarter_files/sky-women.txt
could not find kickstarter_files/beam-us-up-carolena-dayanisma-returns-to-the-mothe.txt
could not find kickstarter_files/waylines-magazine-year-two.txt
could not find kickstarter_files/cornwall-uncovered-map.txt
could no

In [26]:
#col_types = {'kickstarter_page': 'str','funding': 'str', 'campaign_dates': 'str', 'backers': 'str', 'category': 'str', 
#             'description_length': 'int', 'n_pledges': 'int', 'pledge_level_min': 'int', 'pledge_level_max': 'int', 
#             'pledge_level_stddev': 'int', 'currency': 'str'}
#projects.astype(col_types, copy=False, errors='raise', encoding='utf-8')

In [27]:
projects.shape

(72994, 11)

In [28]:
with open('all_data_dirty_3000_7888.pickle', 'wb') as f:
    pickle.dump(projects, f)

In [ ]:
#projects = pd.to_csv('all_data_dirty.csv', index=False)

In [ ]:
#selenium

In [32]:
projects.shape

(72994, 11)

In [11]:
with open('all_data_dirty_1_1999.pickle', 'rb') as f:
    projects = pickle.load(f)

In [14]:
unpopulated_mask = ((projects.description_length == 0) & (projects.pledge_level_min == 0))
populated_mask = ((projects.description_length != 0) | (projects.pledge_level_min != 0))
projects[unpopulated_mask].shape

(75, 11)

In [15]:
proj_dropped = projects[populated_mask]
proj_dropped.shape

(29740, 11)

In [16]:
with open('all_data_dirty_1_1999.pickle', 'wb') as f:
    pickle.dump(proj_dropped, f)

In [30]:
projects.head()

kickstarter_page  \
0         /projects/1883586025/space-comic-in-space/   
1        /projects/1469959370/a-story-without-words/   
2  /projects/burton/lets-talk-calmly-about-securi...   
3  /projects/872190387/schlomos-house-of-gluten-f...   
4  /projects/1715763529/the-cubist-republic-card-...   

                                 funding  \
0      \n\t\t\t\t\tFunding: 540 of 500 (   
1  \n\t\t\t\t\tFunding: 5,007 of 2,000 (   
2  \n\t\t\t\t\tFunding: 2,198 of 1,600 (   
3    \n\t\t\t\t\tFunding: 20 of 55,000 (   
4  \n\t\t\t\t\tFunding: 1,255 of 1,000 (   

                                      campaign_dates                  backers  \
0  \n\t\t\t\t\tCampaign Dates: April 10th -> May ...  \n\t\t\t\t\tBackers: 11   
1  \n\t\t\t\t\tCampaign Dates: April 11th -> May ...  \n\t\t\t\t\tBackers: 58   
2  \n\t\t\t\t\tCampaign Dates: April 25th -> May ...  \n\t\t\t\t\tBackers: 71   
3  \n\t\t\t\t\tCampaign Dates: April 9th -> May 9...   \n\t\t\t\t\tBackers: 2   
4  \n\t\t\t\t\tCampaign Dates: April 9th -> May 9...  \n\t\t\t\t\tBackers: 53   

       category  description_length  n_pledges  pledge_level_min  \
0        Comics                 266          4                10   
1  Film & Video                 581         18                 5   
2    Publishing                 627          5                10   
3          Food                 408          9                 1   
4        Design                 421          8                 5   

   pledge_level_max  pledge_level_stddev currency  
0                50            14.790199        $  
1              5000          1219.176128        $  
2               250            87.040221        $  
3              1000           309.530509        $  
4                45            12.742032        $

In [33]:
projects.currency.value_counts()

$      70394
£       1525
CA       625
AU       284
US       113
NZ        53
Name: currency, dtype: int64

In [36]:
projects.currency.unique()

array(['$', 'US ', 'AU ', '£', 'CA ', 'NZ '], dtype=object)

In [37]:
projects[projects.currency=='US ']

kickstarter_page  \
9            /projects/softinthehead/stinking-heaven/   
12  /projects/59144702/equinox-action-figures-and-...   
1   /projects/1501481976/dishonesty-a-documentary-...   
9   /projects/2080059075/ron-halls-memphis-the-roc...   
3   /projects/northernspark/northern-spark-2014-li...   
6   /projects/1744680204/catch-up-calu-motion-cont...   
7   /projects/255614588/frenchies-artisan-pastries...   
7   /projects/144696345/the-cub-a-student-short-film/   
1   /projects/1868398473/hello-web-app-intro-to-bu...   
12  /projects/1749471818/super-tooth-a-super-fun-a...   
6   /projects/1310339846/hidden-undershirts-6-styl...   
14  /projects/763660817/sam-lachows-2nd-full-lengt...   
5   /projects/588318042/luma-a-smartlamp-for-the-2...   
9              /projects/471947712/legends-of-persia/   
7   /projects/2137768355/havana-motor-club-a-docum...   
7     /projects/1038582734/the-morbid-anatomy-museum/   
14    /projects/1079692033/super-arcade-project-2014/   
4   /projects/lensbaby/creative-focus-lens-for-iph...   
6                 /projects/empiregrown/empire-grown/   
12  /projects/2007974312/sonidos-bolivianos-para-e...   
3   /projects/syncfab/3d-print-or-specialty-fabric...   
5   /projects/814172743/anchored-in-deep-water-the...   
8   /projects/joshfolan/catch-22-based-on-the-unwr...   
3   /projects/skateluger/send-gravity-sport-univer...   
14  /projects/443110891/charlotte-baker-is-haulin-...   
1   /projects/54060271/easyplug-the-sensor-shield-...   
11  /projects/mikedeodato/the-mike-deodato-jr-sket...   
5                          /projects/16128891/sacred/   
7               /projects/786551472/hero-generations/   
9   /projects/1398076023/art-architecture-and-hist...   
..                                                ...   
5           /projects/ordinaryheroes/ordinary-heroes/   
14       /projects/1984252088/robot-army-starter-kit/   
13  /projects/bgreenek/dance-films-builds-an-archive/   
3   /projects/tydennisdrums/3-from-none-ep-ty-denn...   
11             /projects/588680543/roomsies-season-3/   
11  /projects/674276795/yoga-by-numbers-if-you-can...   
1   /projects/gamertalklive/terrene-odyssey-battle...   
1   /projects/1820699218/my-spade-and-me-free-song...   
0   /projects/1275337514/kegbot-internet-beer-kege...   
2   /projects/229805465/rock-paper-scissors-war-a-...   
2      /projects/561467528/savage-the-shard-of-gosen/   
4      /projects/bigelowbrook/growgrip-plant-holders/   
6          /projects/trimr/trimr-water-shaker-bottle/   
9     /projects/1759540378/the-cursed-and-the-damned/   
0   /projects/livid/guitar-wing-wireless-control-s...   
5   /projects/matika/project-562-changing-the-way-...   
11  /projects/638602032/caiberries-early-launch-re...   
11  /projects/2055692701/bru-gear-stainless-steel-...   
9   /projects/lalorek/a-field-guide-to-silicon-hills/   
5               /projects/pixelversion/hey-come-here/   
1       /projects/1084206971/wayward-terran-frontier/   
2   /projects/averystafford/avery-staffords-first-...   
12  /projects/686639804/prinsesa-the-boy-who-dream...   
9   /projects/31957736/ozark-landscapes-augmented-...   
12  /projects/1272467061/worlds-first-patent-pendi...   
14  /projects/1267920717/robert-brueys-third-studi...   
5           /projects/1027447149/dreams-in-the-light/   
13        /projects/1348310034/the-alaska-recordings/   
9   /projects/1306413684/flag-the-app-that-prints-...   
13  /projects/1349306815/strongvolt-smartcharger-t...   

                                      funding  \
9     \n\t\t\t\t\tFunding: 20,077 of 20,000 (   
12     \n\t\t\t\t\tFunding: 7,709 of 20,000 (   
1   \n\t\t\t\t\tFunding: 137,254 of 126,000 (   
9       \n\t\t\t\t\tFunding: 3,063 of 3,000 (   
3     \n\t\t\t\t\tFunding: 20,790 of 20,000 (   
6         \n\t\t\t\t\tFunding: 84 of 20,000 (   
7     \n\t\t\t\t\tFunding: 41,193 of 39,750 (   
7       \n\t\t\t\t\tFunding: 4,111 of 4,000 (   
1      \n\t\t\t\t\tFunding: 12,136 of 7,000 (   
12      \n\t